# Liouvilles Theorem

In der Computerphysik haben Sie eine Reihe von Methoden kennengelernt, um Differentialgleichungen zu lösen. Diese und noch viele weitere sind im Paket [``DifferentialEquations``](https://github.com/JuliaDiffEq/DifferentialEquations.jl) implementiert. In diesem Notebook zeigen wir Ihnen, wie Sie dies verwenden können, um das Liouville Theorem anhand dreier Beispiele besser kennenzulernen.

In [ ]:
Pkg.add("DifferentialEquations")

In [ ]:
using DifferentialEquations
using PyCall
using PyPlot
pygui(true)

In [ ]:
function handle_close(event)
    global update_figure
    update_figure = false
    print("Figure closed")
end

### Definition der drei Hamiltonians

In [ ]:
function oscillator(t, u, du)
    du[1] = u[2]
    du[2] = -u[1]
end

function hamiltonian(t,u,du)
# Hier die Bewegungsgleichungen des gegeben Hamiltonians (6) implementieren
end

function damped_oscillator(t, u, du)
# Hier die Bewegungsgleichungen des gedämpften Oszillators implementieren
end

### Auswahl der Modells und Erzeugung der Zeitreihen

In [ ]:
h = oscillator # Wahl des Modells

xs = Array{Float64}[] # Array um die Zeitreihen der x-Achse zu speichern
ys = Array{Float64}[] # Array um die Zeitreihen der y-Achse zu speichern
ts = (0. , 50.) # Start und Endzeit der Simulation

# Teilchen
# Veraendern Sie die Schleife so, dass alle Koordinaten in einem Kreis
# mit Radius 5 um den Ursprung liegen. Als Abstand zwischen den Punkten
# koennen Sie auf jeder Achse 0.2 auswaehlen
for x in [-3.]
    for y in [3.]
        init = [x, y] # Anfangsbedingung initialisieren
        prob = ODEProblem(h, init, ts) # Definiere DGL Problem mit Modell, Anfangsbedingung, Zeitrahmen
        sol = solve(prob, RK4(), dt=0.1, adaptive=false) # Loese Problem mit Runge Kutta 4. Ordnung, Zeitschritt 0.1, kein adaptiver Zeitschritt        
        push!(xs, sol[1, :]) # Zeitreihen abspeichern
        push!(ys, sol[2, :])
    end
end

# Rand
# Veraendern Sie die Schleife so, dass alle Koordinaten in einem Kreis
# mit Radius  5 < r < 5.2 um den Ursprung liegen. Als Abstand zwischen den Punkten
# koennen Sie auf jeder Achse 0.05 auswaehlen
bound_xs = Array{Float64}[]
bound_ys = Array{Float64}[]

for x in [4.]
    for y in [0.1]
        init = [x, y] # Anfangsbedingung initialisieren
        prob = ODEProblem(h, init, ts) # Definiere DGL Problem mit Modell, Anfangsbedingung, Zeitrahmen
        sol = solve(prob, RK4(), dt=0.1, adaptive=false) # Loese Problem mit Runge Kutta 4. Ordnung, Zeitschritt 0.1, kein adaptiver Zeitschritt        
        push!(bound_xs, sol[1, :]) # Zeitreihen abspeichern
        push!(bound_ys, sol[2, :])
    end
end

### Grafische Darstellung als Animation

In [ ]:
# Initiale Teilchenpositionen
px = [x[1] for x in xs] 
py = [y[1] for y in ys]

# Initiale Randpositionen
bpx = [x[1] for x in bound_xs]
bpy = [y[1] for y in bound_ys]

# Diese beiden Teilchen verfolgen wir extra
# setze i2 auf anderen Wert sobald mehrere Teilchen verfuegbar
i1 = 1
i2 = 1

# Fenster erzeugen
fig = figure(figsize=(5,5))
fig[:canvas][:mpl_connect]("close_event", handle_close)

# Ausgangskonfiguration plotten
s, = plot(px, py, "o", alpha=0.2)
b, = plot(bpx, bpy, "o", color="black", markersize=2)
s1, = plot(px[i1], py[i1], "s")
s2, = plot(px[i2], py[i2], "s")

# Aufhuebschen
axis("off")
xlim([-10, 10])
ylim([-10, 10])

update_figure = true

# Schleife fuer Animation
for i in 1:500
    px = [x[i] for x in xs]
    py = [y[i] for y in ys]
    bpx = [x[i] for x in bound_xs]
    bpy = [y[i] for y in bound_ys]

    
    s[:set_data](px, py)
    b[:set_data](bpx, bpy)
    s1[:set_data](px[i1], py[i1])
    s2[:set_data](px[i2], py[i2])
    pause(0.0001)
end